In [1]:
print("Processing... ", end = "")
import sys
import ROOT
from ROOT import gROOT
from ROOT import gStyle
%jsroot on

ROOT.gInterpreter.AddIncludePath('../../include/')
ROOT.gInterpreter.Declare('#include "RoEvent.h"')
ROOT.gSystem.Load('../../libs/libRoEvent.so')

gROOT.LoadMacro("../style/CMS/tdrstyle.C")
gROOT.ProcessLine("setTDRStyle();")
gROOT.LoadMacro("../style/CMS/CMS_lumi.C")

from array import array
from pathlib import Path
import numpy as np
from scipy import signal
from scipy.signal import find_peaks, peak_widths
sys.path.append("../package/")

import lycro as lyplot

gStyle.SetOptFit(0)

Processing... Welcome to JupyROOT 6.24/00


In [2]:
print("Processing... ", end = "")
run = "r75"; date = " Wed Jul 21 2021"; root = "../../tmp/sig_" + run + ".root"
elog = "https://elog.ip2i.in2p3.fr/wa105/Cold-Box+CERN+Installation/6"
inj = "30dB: 500mv -> 15.8mV"
comment = "Pulsing a single channel per card."
chs = range(0, 640); 
cards = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
mapCards = ["70", "102", "8", "9", "38", "2-3", "98", "81", "2-1", "49"]

window = 45; pads = [10, 35]; pad = int(window/2); 
threshold = 200; 
pols = [1, -1]; 
exptSigPerEvent = [12, 11];

size = 1000

pathToSave = "../../tmp/" + run + "/fig/"
pdf = "../../tmp/" + run + "/viewer_" + run + ".tex"
Path("../../tmp/" + run).mkdir(parents=True, exist_ok=True)
Path("../../tmp/" + run + "/fig").mkdir(parents=True, exist_ok=True)

print("Done")

Processing... Done


In [3]:
print("Processing... ", end = "")

fh = ROOT.TFile(root)
head = "header" + "_thr" + str(threshold) + "_wind" + str(window)
numev = 0
for entry in fh.Get(head): 
    numev = entry.main.numev

affixes = {}; params = {}
thds = {};
for pol in pols:
    affix = ""
    if(pol == 0): affix = "_wrong"
    if(pol == 1): affix = "_pos"
    if(pol == -1): affix = "_neg"
    affixes[pol] = affix
    
    name = "evchhit_prof" + affix; hist = ROOT.TH2D(name, name, numev, 0, numev, len(chs), chs[0], chs[-1]); thds[name] = hist
    name = "profile_clean" + affix; hist = ROOT.TH2D(name, name, window, 0, window, 4096, 0, 4096); thds[name] = hist
    name = "profile_dev" + affix; hist = ROOT.TH2D(name, name, window, 0, window, 4096, 0, 4096); thds[name] = hist
    name = "profile_raw" + affix; hist = ROOT.TH2D(name, name, window, 0, window, 4096, 0, 4096); thds[name] = hist
    name = "profile_bad" + affix; hist = ROOT.TH2D(name, name, window, 0, window, 4096, 0, 4096); thds[name] = hist
    
    name = "peaks_dev" + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
    name = "height_dev" + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
    name = "sum_dev" + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
    
    name = "height_clean" + affix;  hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
    name = "sum_clean" + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
    
    name = "pedestal_dev" + affix; hist = ROOT.TH2D(name, name, window, 0, window, 4096, 0, 4096); thds[name] = hist
    name = "pedestal_clean" + affix; hist = ROOT.TH2D(name, name, window, 0, window, 4096, 0, 4096); thds[name] = hist
    
    name = "profile_cut" + affix; hist = ROOT.TH2D(name, name, window, 0, window, 4096, 0, 4096); thds[name] = hist
    name = "weights" + affix; hist = ROOT.TH1D(name, name, window, 0, window); thds[name] = hist
    name = "power_in" + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
    name = "power_out" + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
    name = "power_2d" + affix; hist = ROOT.TH2D(name, name, size, 1, -1, size, 1, -1); thds[name] = hist
    
    for ch in chs:
        name = "height_dev_ch" + str(ch) + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
        name = "sum_dev_ch" + str(ch) + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
        name = "pedestal_dev_ch" + str(ch) + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
        
        name = "height_clean_ch" + str(ch) + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
        name = "sum_clean_ch" + str(ch) + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
        name = "pedestal_clean_ch" + str(ch) + affix; hist = ROOT.TH1D(name, name, size, 1, -1); thds[name] = hist
        
    name = "ped_mean" + affix; params[name] = 2048
    name = "ped_rms" + affix; params[name] = 0
    name = "profile_N_clean" + affix; params[name] = 0
    name = "profile_N_dev" + affix; params[name] = 0
    name = "profile_clean_ymin" + affix; params[name] = 4096
    name = "profile_clean_ymax" + affix; params[name] = 0
    name = "evchhit_list" + affix; params[name] = []
    
    name = "refSig" + affix; params[name] = []
    
    name = "refSig_sum" + affix; params[name] = 0
    name = "refSig_power" + affix; params[name] = 0
    name = "linker_bad" + affix; params[name] = {}
print("Done")

Processing... Done


In [4]:
print("ROOT file (RoSig class): {} \n".format(root))
for pol in pols:
    nSig = 0; nGoodSig = 0;
    affix = affixes.get(pol)    
    
    prof_raw = thds.get("profile_raw" + affix)
    prof_dev = thds.get("profile_dev" + affix)
    peaks_dev = thds.get("peaks_dev" + affix)
    ped_dev = thds.get("pedestal_dev" + affix)
    hSum = thds.get("sum_dev" + affix)
    hHeight = thds.get("height_dev" + affix)
    evchhit = thds.get("evchhit_prof" + affix)
    
    f = ROOT.TFile(root)
    treeName = affix[1:] + "_thr" + str(threshold) + "_wind" + str(window)
    tree = f.Get(treeName);
    isig = 0; numSigs = tree.GetEntries()
    for entry in tree:
        sig = entry.sigs; isig += 1;
        if(isig%100 == 0 or isig == numSigs): 
            print("Tree: {}; Sig {}:{} is processing...".format(treeName, isig, numSigs), end='\r');
        
        card = sig.card; ch = sig.ch
        if(not(ch in chs and card in cards)): continue
        if(sig.pol != pol): continue
        
        #filling all signals
        evchhit.Fill(sig.event, sig.ch)
        
        if(len(sig.signal) != len(sig.pedestal)): continue
        npeaks = len(sig.peaks)
        nSig += 1; 
        if(npeaks == 1):
            if(sig.unequal == 0):
                nGoodSig += 1;
                peaks_dev.Fill(sig.peaks[0])
        else: continue
        for i in range(len(sig.signal)):
            prof_raw.Fill(i, sig.signal[i])
            if(npeaks == 1): 
                prof_dev.Fill(i, sig.signal[i])
                ped_dev.Fill(i, sig.pedestal[i])
        
        integral = sig.sum
        hSum.Fill(integral); 
        thds.get("sum_dev_ch" + str(ch) + affix).Fill(integral)
        
        height = sig.height 
        hHeight.Fill(height); 
        thds.get("height_dev_ch" + str(ch) + affix).Fill(height)
        thds.get("pedestal_dev_ch" + str(ch) + affix).Fill(sig.level)
        
    pedestal = round(thds.get("pedestal_dev" + affix).ProjectionY().GetMean()); params["ped_mean" + affix] = pedestal
    rms = round(thds.get("pedestal_dev" + affix).ProjectionY().GetRMS()); params["ped_rms" + affix] = rms
    params["profile_N_dev" + affix] = nGoodSig
    print("\nSignals in Frofile: {} ({})".format(nSig, nGoodSig), "\n")

ROOT file (RoSig class): ../../tmp/sig_r75.root 

Tree: pos_thr200_wind45; Sig 360196:360196 is processing...
Signals in Frofile: 360196 (316688) 

Tree: neg_thr200_wind45; Sig 336897:336897 is processing...
Signals in Frofile: 336897 (290423) 



In [5]:
print("Processing... ", end = "")
#get wrong signals ffom calib
def wrongEvents(prof, chs, numev, expected):
    result = []
    for ch in chs:
        for ev in range(numev):
            if(prof.GetBinContent(ev,ch) != expected and prof.GetBinContent(ev,ch) !=0):
                result.append(ev)
    return set(result)

for pol in pols:
    expected = 0
    affix = affixes.get(pol)    
    evchhit = thds.get("evchhit_prof" + affix)
    if(pol == 1): expected = 12
    if(pol == -1): expected = 11
    params["evchhit_list" + affix] = wrongEvents(evchhit, chs, numev, expected)

print("\nPOS: ", params["evchhit_list_pos"])
print("NEG: ", params["evchhit_list_neg"])
print("Done")

Processing... 
POS:  {775, 2728, 776, 1426, 1427, 2077}
NEG:  {775, 2728, 776, 1426, 1427, 2077}
Done


In [6]:
print("Processing... ", end = "")
def cutProfile(out, prof, norm, rms, y, x):
    rms = round(rms)
    i = y; isDel = False
    while i > 0:
        if(i < y - 6*rms): isDel = True
        if(isDel): out.SetBinContent(x, i, 0)
        else: 
            value = prof.GetBinContent(x, i)
            if(norm > 0): value = value/norm
            out.SetBinContent(x, i, value)
        i = i - 1;
    i = y; isDel = False
    while i < 4096:
        if(i > y + 6*rms): isDel = True
        if(isDel): out.SetBinContent(x, i, 0)
        else:
            value = prof.GetBinContent(x, i)
            if(norm > 0): value = value/norm
            out.SetBinContent(x, i, value)
        i = i + 1;    

for pol in pols:
    affix = affixes.get(pol)                                
    
    prof_cut = thds.get("profile_cut" + affix)
    weights = thds.get("weights" + affix)
    prof_dev = thds.get("profile_dev" + affix)
    ped_mean = params.get("ped_mean" + affix)
    ped_rms = params.get("ped_rms" + affix)
    refSig = params.get("refSig" + affix)
    refSig_sum = 0; refSig_power = 0 
    
    for x in range(1, window+1):
        tmp = [];
        for y in range(4096):
            tmp.append(prof_dev.GetBinContent(x, y))
        ymax = np.argmax(tmp); vmax = np.max(tmp);
        refSig.append(ymax); weights.SetBinContent(x, pol*(ymax - ped_mean))
        refSig_sum += ymax - ped_mean; refSig_power += pow((ymax - ped_mean), 2) 
        cutProfile(prof_cut, prof_dev, vmax, ped_rms, int(ymax), int(x))
    
    norm = weights.GetBinContent(weights.GetMaximumBin())
    if(norm > 0):
        for n in range(1, window+1):
            nbin = weights.GetBinContent(n)
            weights.SetBinContent(n, nbin/norm)
        
    params["refSig_sum" + affix] = refSig_sum
    params["refSig_power" + affix] = refSig_power
print("Done")

Processing... Done


In [7]:
def fillProf(prof, sig):
    for s in range(len(sig)):
        prof.Fill(s, sig[s])
def fillProfLinked(prof, linker, sig):
    for s in range(len(sig.signal)):
        prof.Fill(s, sig.signal[s])
        
        triplet = (sig.event, sig.card, sig.ch, sig.peak)
        pair = (s, sig.signal[s])
        new = [];
        prev = linker.get(pair)
        if(type(prev) != type(new)): new.append(triplet);
        else:
            new.extend(prev); new.append(triplet);
        linker[pair] = new
        #print(pair, linker[pair])
        
# Let's do filtering 
print("ROOT file (RoSig class): {} \n".format(root))
sigs = []
for pol in pols:
    nSig = 0;
    affix = affixes.get(pol)
    
    linker_bad = params.get("linker_bad" + affix)
    prof_bad = thds.get("profile_bad" + affix); 
    prof_clean = thds.get("profile_clean" + affix);
    prof_cut = thds.get("profile_cut" + affix)
    power_in = thds.get("power_in" + affix)
    power_out = thds.get("power_out" + affix)
    power_inOut = thds.get("power_2d" + affix)
    weights = thds.get("weights" + affix)
    ped_mean = params.get("ped_mean" + affix)
    ped_clean = thds.get("pedestal_clean" + affix)
    
    ch_list = params["evchhit_list" + affix]
    
    hSum = thds.get("sum_clean" + affix)
    hHeight = thds.get("height_clean" + affix)
    
    f = ROOT.TFile(root)
    treeName = affix[1:] + "_thr" + str(threshold) + "_wind" + str(window)
    tree = f.Get(treeName);
    isig = 0; numSigs = tree.GetEntries()
    for entry in tree:
        sig = entry.sigs; isig += 1;
        if(isig%100 == 0 or isig == numSigs): 
            print("Tree: {}; Sig {}:{} is processing...".format(treeName, isig, numSigs), end='\r');
        card = sig.card; ch = sig.ch    
        if(not(ch in chs and card in cards)): continue
        if(ch in ch_list):  continue
        if(sig.pol != pol): continue
        if(sig.unequal == 1): continue
        if(len(sig.signal) != len(sig.pedestal)): 
            fillProfLinked(prof_bad, linker_bad, sig); 
            continue
        npeaks = len(sig.peaks)
        if(npeaks > 1): 
            fillProfLinked(prof_bad, linker_bad, sig);  
            continue
        
        pOut = 0; pIn = 0; wpOut = 0; wpIn = 0
        for i in range(len(sig.signal)):
            cell = prof_cut.GetBinContent(i+1, sig.signal[i]);
            weight = weights.GetBinContent(i+1)
            if(cell == 0): 
                pOut += pow((sig.signal[i] - ped_mean), 2);
                wpOut += (1-weight)*pow((sig.signal[i] - ped_mean), 2)
            if(cell > 0): 
                pIn += pow((sig.signal[i] - ped_mean), 2);
                wpIn += (1-weight)*pow((sig.signal[i] - ped_mean), 2);
        if(wpOut < wpIn):
            nSig +=1
            fillProf(prof_clean, sig.signal)
            fillProf(ped_clean, sig.pedestal)
            
            integral = sig.sum
            hSum.Fill(integral); 
            thds.get("sum_clean_ch" + str(ch) + affix).Fill(integral)
        
            height = sig.height 
            hHeight.Fill(height); 
            thds.get("height_clean_ch" + str(ch) + affix).Fill(height)
            thds.get("pedestal_clean_ch" + str(ch) + affix).Fill(sig.level)           
        else: 
            fillProfLinked(prof_bad, linker_bad, sig);
        power_inOut.Fill(pIn, pOut); power_out.Fill(pOut); power_in.Fill(pIn)
    params["profile_N_clean" + affix] = nSig
    print("\nSignals in Frofile: {}".format(nSig), "\n")

ROOT file (RoSig class): ../../tmp/sig_r75.root 

Tree: pos_thr200_wind45; Sig 360196:360196 is processing...
Signals in Frofile: 316066 

Tree: neg_thr200_wind45; Sig 336897:336897 is processing...
Signals in Frofile: 290002 



In [22]:
def drawProf(pol, affix, path2Save, thds, params):

    affixPol = affixes.get(pol)
    plot = thds.get("profile_" + affix + affixPol).Clone()
    ped = thds.get("pedestal_" + affix + affixPol)
    hSum = thds.get("sum_" + affix + affixPol)
    hHeight = thds.get("height_" + affix + affixPol)
    hmax = 0
    for i in range(int(hHeight.GetNbinsX())):
        if(hHeight.GetBinContent(i) > 0):
            hmax = hHeight.GetXaxis().GetBinCenter(i);
            
    N = params["profile_N_" + affix + affixPol];

    ped_level = ped.ProjectionY().GetMean()
    height_level = hHeight.GetMean()

    name = "h={:.2f}+-{:.2f}, sum={:.2f}+-{:.2f}, ped={:.2f}+-{:.2f}, N={} | {} | {}".format(hHeight.GetMean(), hHeight.GetMeanError(), hSum.GetMean(),  hSum.GetMeanError(), ped.ProjectionY().GetMean(), ped.ProjectionY().GetMeanError(), N, str(run), plot.GetName()) 
    cName = plot.GetName(); cTitle = "c"; cX = 800; cY = 600
    c = ROOT.TCanvas(cName, cTitle, cX, cY)


    #---
    iPeriod = "0"; iPos="0"
    #---
    gROOT.ProcessLine("cmsText = \"\";")
    gROOT.ProcessLine("writeExtraText = true;")
    gROOT.ProcessLine("extraText  = \"\";") 
    gROOT.ProcessLine("lumi_sqrtS = \"" + name + "\";") 

    plot.GetXaxis().SetTitle("tick"); plot.GetYaxis().SetTitle("ADCu"); plot.GetZaxis().SetTitle("numsig")

    if(pol == 1): plot.GetYaxis().SetRangeUser(ped_level - 6*ped.GetRMS(), ped_level+hmax + 6*hHeight.GetRMS());
    if(pol == -1): plot.GetYaxis().SetRangeUser(ped_level-hmax - 6*hHeight.GetRMS(), ped_level + 6*ped.GetRMS());
    p1 = ROOT.TPad("p1", "", 0, 0, 1, 1);
    p1.SetGrid();

    p1.SetTopMargin(0.07)
    p1.SetRightMargin(0.20)
    p1.Draw();
    p1.cd();
    plot.Draw("colz"); 
    cms_lumi_str = "CMS_lumi("+cName+", "+iPeriod+", "+iPos+");"; gROOT.ProcessLine(cms_lumi_str)

    c.Update()
    c.SaveAs(path2Save + cName + ".svg");
    c.SaveAs(path2Save + cName + ".pdf");
    plot.SaveAs(path2Save + cName + ".root");

    
def drawChEv(pol, path2Save, thds, params):

    affixPol = affixes.get(pol)
    plot = thds.get("evchhit_prof" + affixPol)
    ev_list = params["evchhit_list" + affixPol]
    events = ""
    for ev in ev_list:
        events += str(ev)
        events += " "

    name =  plot.GetName() + " | Wrong Events: " + events
    cName = plot.GetName(); cTitle = "c"; cX = 1000; cY = 350
    c = ROOT.TCanvas(cName, cTitle, cX, cY)


    #---
    iPeriod = "0"; iPos="0"
    #---
    gROOT.ProcessLine("cmsText = \"\";")
    gROOT.ProcessLine("writeExtraText = true;")
    gROOT.ProcessLine("extraText  = \"\";") 
    gROOT.ProcessLine("lumi_sqrtS = \"" + name + "           " + "\";") 

    plot.GetXaxis().SetTitle("evnum"); plot.GetYaxis().SetTitle("ch"); plot.GetZaxis().SetTitle("numsig")

    p1 = ROOT.TPad("p1", "", 0, 0, 1, 1);
    p1.SetGrid();

    p1.SetTopMargin(0.07)
    p1.SetRightMargin(0.15)
    p1.Draw();
    p1.cd();
    plot.Draw("colz"); 
    cms_lumi_str = "CMS_lumi("+cName+", "+iPeriod+", "+iPos+");"; gROOT.ProcessLine(cms_lumi_str)

    c.Update()
    c.SaveAs(path2Save + cName + ".svg");
    c.SaveAs(path2Save + cName + ".pdf");
    plot.SaveAs(path2Save + cName + ".root");
    

def drawMultiGraph(name, path2Save, grs):
    
    cName = name; cTitle = "c"; cX = 1000; cY = 350
    c = ROOT.TCanvas(cName, cTitle, cX, cY)
    
    plot = ROOT.TMultiGraph();
    for gr in grs: 
        plot.Add(gr); 
    #---
    iPeriod = "0"; iPos="0"
    #---
    gROOT.ProcessLine("cmsText = \"\";")
    gROOT.ProcessLine("writeExtraText = true;")
    gROOT.ProcessLine("extraText  = \"\";") 
    gROOT.ProcessLine("lumi_sqrtS = \"" + name + "           " + "\";") 

    plot.GetXaxis().SetTitle("ch"); plot.GetYaxis().SetTitle("ADCu"); 

    p1 = ROOT.TPad("p1", "", 0, 0, 1, 1);
    p1.SetGrid();

    p1.SetTopMargin(0.07)
    p1.SetRightMargin(0.15)
    p1.Draw();
    p1.cd();
    plot.Draw("AP"); 
    cms_lumi_str = "CMS_lumi("+cName+", "+iPeriod+", "+iPos+");"; gROOT.ProcessLine(cms_lumi_str)

    c.Update()
    c.SaveAs(path2Save + cName + ".svg");
    c.SaveAs(path2Save + cName + ".pdf");
    plot.SaveAs(path2Save + cName + ".root");

def figs2latex(path2First, path2Second, caption, label):
    output = "\\begin{figure}[h!]\n"
    output += "\\begin{minipage}[h]{0.47\linewidth}\n"
    
    output += "\\center{\includegraphics[width=1\linewidth]{"
    output += path2First
    output += "}} \n"
    
    output += "\\end{minipage} \n"
    output += "\\hfill \n"
    output += "\\begin{minipage}[h]{0.47\linewidth} \n"
    
    output += "\\center{\includegraphics[width=1\linewidth]{"
    output += path2Second
    output += "}} \n"
    
    output += "\\end{minipage} \n"
    
    #output += "\\caption{"
    #output += caption
    #output += "} \n"
    
    #output += "\\label{"
    #output += label
    #output += "} \n"
    
    output += "\\end{figure} \n"
    output += "\\FloatBarrier \n"
    
    return output

def fig2latex(path2File, caption, label):
    output = "\\begin{figure}[h!]\n"
    
    output += "\\center{\includegraphics[width=1\linewidth]{"
    output += path2File
    output += "}} \n"
    
    #output += "\\caption{"
    #output += caption
    #output += "} \n"
    
    #output += "\\label{"
    #output += label
    #output += "} \n"
    
    output += "\\end{figure} \n"
    output += "\\FloatBarrier \n"
    
    return output

def includes2latex(text):
    
    text += '\\documentclass[12pt, a4paper]{article}\n'
    text += ('\\usepackage[utf8]{inputenc}\n')
    text += ('\\usepackage[english]{babel}\n')
    text += ('\\usepackage[T1]{fontenc}\n')
    text += ('\\usepackage{graphicx}\n')
    text += ('\\usepackage{geometry}\n')
    text += ('\\usepackage{color,soul}\n')
    text += ('\\DeclareRobustCommand{\hlcyan}[1]{{\sethlcolor{cyan}\hl{#1}}}\n')
    text += ('\\usepackage[document]{ragged2e}\n')
    text += ('\\usepackage{array}\n')
    text += ('\\usepackage{graphicx}\n')
    text += ('\\usepackage{placeins}\n')
    text += ('\\usepackage{amssymb}\n')
    text += ('\\usepackage{wrapfig}\n')
    text += ('\\usepackage{hyperref}\n')
    text += ('\\usepackage{listings}\n')
    
    text += ('\\newcommand{\+}[1]{\ensuremath{\mathbf{#1}}}\n')
    text += ('\\geometry{top=2.5cm, bottom=2.5cm, right=2.5cm, left=2.5cm}\n')
    return text

def main2latex(text, date, run, inj, comment, mapCards, threshold, pads, exptSigPerEvent, elog):
    text += ('\\noindent Institut de Physique des 2 Infinis de Lyon \hfill ' + str(date) + ', CERN NP02 \\\\ \n')
    text += ('\\center\n')
    text += ('\\section*{Signal View: Run-' + str(run) + '} \n')
    text += ('ELOG: ' + str(elog) + ' \\\\ \n')
    text += ('GitHub: (https://github.com/shchablo/CRO) \\\\ \n')
    text += ('\\justify\n')
    text += ('Comment: ' + comment + ' \\\\ \n')
    text += ('Signal: ' + inj + "; per event: pos-" + str(exptSigPerEvent[0])+":neg-"+ str(exptSigPerEvent[1]) + ' \\\\ \n')
    text += ('Threshold: ' + str(threshold) + " ADCu: Pad: " + str(pads[0]) + ":" + str(pads[1]) +" ticks" + ' \\\\ \n')
    text += ('AMC Cards: ' )
    for card in mapCards: 
        text += card + " "
    text += ' \\\\ \n'
    text += ('Crate: 40G C2 - chimney No. 1 \n')
    
   
    #text += ('\\tableofcontents\n')
    return text 
def page2latex():
    return result
def example2latex():
    result = ""
    return result
def ch2plot(name, affix, chs, thds):
    x, xerr, y, yerr = array( 'd' ), array( 'd' ), array( 'd' ), array( 'd' )
    for ch in chs:
        iname = name + str(ch) + affix; 
        mean = thds.get(iname).GetMean()
        errMean = thds.get(iname).GetMeanError()
        x.append(ch); xerr.append(0)
        y.append(mean); yerr.append(errMean)
    gr = ROOT.TGraphErrors(len(x),x,y,xerr,yerr);
    return gr
        

In [23]:

latex = ""
latex = includes2latex(latex)
latex += "\\begin{document}\n"
latex = main2latex(latex, date, run, inj, comment, mapCards, threshold, pads, exptSigPerEvent, elog)

if( -1 in pols and 1 in pols):
    
    drawProf(1, "clean", pathToSave, thds, params); drawProf(-1, "clean", pathToSave, thds, params); 
    latex += figs2latex(pathToSave + "profile_clean_pos.pdf", pathToSave + "profile_clean_neg.pdf", "profile clean", "Label")
    
    #drawProf(1, "dev", pathToSave, thds, params); drawProf(-1, "dev", pathToSave, thds, params); 
    #latex += figs2latex(pathToSave + "profile_dev_pos.pdf", pathToSave + "profile_dev_neg.pdf", "profile dev", "Label")
    
    drawChEv(1, pathToSave, thds, params); drawChEv(-1, pathToSave, thds, params); 
    latex += fig2latex(pathToSave + "evchhit_prof_pos.pdf", "evchhit prof pos", "Label")
    latex += fig2latex(pathToSave + "evchhit_prof_neg.pdf", "evchhit prof neg", "Label")
    
    peds = []
    peds.append(ch2plot("pedestal_clean_ch", "_pos", chs, thds)); 
    peds.append(ch2plot("pedestal_clean_ch", "_neg", chs, thds))
    drawMultiGraph("pedestal_clean", pathToSave, peds)
    latex += fig2latex(pathToSave + "pedestal_clean.pdf", "pedestals clean", "Label")
    
latex += "\\end{document}\n"

with open(pdf,'w') as file:
    file.write(latex)

h=352.70+-0.02, sum=2597.00+-0.18, ped=2037.09+-0.00, N=316066 | r75 | profile_clean_pos
h=362.29+-0.02, sum=2603.53+-0.18, ped=2036.81+-0.00, N=290002 | r75 | profile_clean_neg
evchhit_prof_pos | Wrong Events: 775 2728 776 1426 1427 2077            
evchhit_prof_neg | Wrong Events: 775 2728 776 1426 1427 2077            
pedestal_clean           


Info in <TCanvas::Print>: SVG file ../../tmp/r75/fig/profile_clean_pos.svg has been created
Info in <TCanvas::Print>: pdf file ../../tmp/r75/fig/profile_clean_pos.pdf has been created
Info in <TH2D::SaveAs>: ROOT file ../../tmp/r75/fig/profile_clean_pos.root has been created
Info in <TCanvas::Print>: SVG file ../../tmp/r75/fig/profile_clean_neg.svg has been created
Info in <TCanvas::Print>: pdf file ../../tmp/r75/fig/profile_clean_neg.pdf has been created
Info in <TH2D::SaveAs>: ROOT file ../../tmp/r75/fig/profile_clean_neg.root has been created
Info in <TCanvas::Print>: SVG file ../../tmp/r75/fig/evchhit_prof_pos.svg has been created
Info in <TCanvas::Print>: pdf file ../../tmp/r75/fig/evchhit_prof_pos.pdf has been created
Info in <TH2D::SaveAs>: ROOT file ../../tmp/r75/fig/evchhit_prof_pos.root has been created
Info in <TCanvas::Print>: SVG file ../../tmp/r75/fig/evchhit_prof_neg.svg has been created
Info in <TCanvas::Print>: pdf file ../../tmp/r75/fig/evchhit_prof_neg.pdf has been c

In [12]:
affix = "_neg"
prof_cut = thds.get("profile_cut" + affix)
prof_bad = thds.get("profile_bad" + affix)
peaks_dev = thds.get("peaks_dev" + affix)
evchhit = thds.get("evchhit_prof" + affix)
plot = evchhit.Clone()

cName = "c"; cTitle = "c"; cX = 1000; cY = 320
c = ROOT.TCanvas(cName, cTitle, cX, cY)
#c.SetGrid()
#---

p1 = ROOT.TPad("p1", "", 0, 0, 1, 1);
p1.SetGrid();

# Draw the 1st TMultiGraph
p1.SetBottomMargin(0.2)
#p1.SetRightMargin(0.15)
p1.Draw();
p1.cd();
plot.Draw("colz"); 

c.Draw()


In [13]:
affix = "_pos"
linker_bad = params.get("linker_bad" + affix)
pair = (16, 2380); 
print("x, y: {}".format(pair))
print("ev, card, ch, peak: {}".format(linker_bad[pair]))

x, y: (16, 2380)


KeyError: (16, 2380)